In [68]:
import pandas as pd # data processing
import pandas_profiling as pp
import numpy as np # linear algebra

In [104]:
import pprint #indet json 
import requests #make http requests
from qwikidata.sparql  import return_sparql_query_results #return sparql results
from SPARQLWrapper import SPARQLWrapper, JSON #questo serve a vedere la struttura delle risposte
import ssl
from http.client import IncompleteRead
import time
import urllib.error
from xml.etree.ElementPath import xpath_tokenizer_re

In [2]:
mid_df = pd.read_csv('mid_half.csv')
first_half = pd.read_csv('first_half.csv')
last_half = pd.read_csv('last_half.csv')

In [3]:
frames = [first_half, mid_df, last_half]

new_id_dataset = pd.concat(frames)

In [4]:
print(len(first_half))
print(len(last_half))
print(len(mid_df))
print(len(new_id_dataset))

1588
1729
2161
5478


In [5]:

new_id_dataset = new_id_dataset.loc[:, ~new_id_dataset.columns.str.contains('^Unnamed')]
new_id_dataset.reset_index(level=None, drop=True, inplace=True, col_level=0, col_fill='')
new_id_dataset.head(5)

id                             title  year
0  tt11394180              Dick Johnson Is Dead  2020
1   tt0108041                           Sankofa  1993
2   tt5164438                      The Starling  2021
3  tt15204288  Confessions of an Invisible Girl  2021
4   tt0139872                   Avvai Shanmughi  1996

In [6]:
len(new_id_dataset)

5478

In [7]:
new_id_dataset1 = new_id_dataset.copy()

In [8]:
df_id =  new_id_dataset1.replace('no_data', np.nan)

In [99]:
df_id.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 5619 entries, 0 to 5618
Data columns (total 3 columns):
 #   Column  Non-Null Count  Dtype 
---  ------  --------------  ----- 
 0   id      5619 non-null   object
 1   title   5619 non-null   object
 2   year    5619 non-null   int64 
dtypes: int64(1), object(2)
memory usage: 131.8+ KB


In [9]:
pd.concat(g for _, g in new_id_dataset.groupby("id") if len(g) > 1)

id                            title  year
2815  tt0091607          Martial Arts of Shaolin  1986
4127  tt0091607          Martial Arts of Shaolin  1986
372   tt0103671                      American Me  1992
5195  tt0103671                      American Me  1992
3935  tt0118980                 Digging to China  1998
3936  tt0118980                 Digging to China  1998
2350  tt0806203                         Carriers  2009
3981  tt0806203                         Carriers  2009
2793  tt0951216                        Mad Money  2008
4131  tt0951216                        Mad Money  2008
2728  tt1103153                          Killers  2010
5353  tt1103153                          Killers  2010
3333  tt1265990                     The Roommate  2011
4865  tt1265990                     The Roommate  2011
2785  tt1638002                      Love, Rosie  2014
4401  tt1638002                      Love, Rosie  2015
842   tt2123342                        Underdogs  2013
3534  tt2123342                        Underdogs  2013
943   tt3173910                 Hasee Toh Phasee  2014
4602  tt3173910                 Hasee Toh Phasee  2014
3107  tt3283864                      Some Freaks  2017
5425  tt3283864                      Some Freaks  2017
2232  tt4325400  APEX: The Story of the Hypercar  2016
4030  tt4325400  APEX: The Story of the Hypercar  2016
2749  tt4327752                  Lady Bloodfight  2016
4243  tt4327752                  Lady Bloodfight  2017
2968  tt4505666               Prescription Thugs  2015
3731  tt4505666               Prescription Thugs  2015
2594  tt5239942                             Heal  2017
3870  tt5239942                             Heal  2017
3104  tt5639898                   Social Animals  2018
3682  tt5639898                   Social Animals  2018
2642  tt5918090           I Am Not Madame Bovary  2016
4443  tt5918090           I Am Not Madame Bovary  2016
2181  tt6041458                        Abhinetri  2016
4798  tt6041458                        Abhinetri  2016
3297  tt6150238                        The Mayor  2017
3298  tt6150238                        The Mayor  2017
1909  tt6998596                          Rangoon  2017
5000  tt6998596                          Rangoon  2017
1587  tt7133686                         Next Gen  2018
1588  tt7133686                         Next Gen  2018
1390  tt7329858                             Pari  2018
3740  tt7329858                             Pari  2018
28    tt8009744                            Worth  2021
4615  tt8009744                            Worth  2021

In [10]:
new_id_dataset_copy = new_id_dataset.drop_duplicates(keep='first')
len(new_id_dataset_copy)

5457

In [12]:
new_id_dataset_copy["id"]

0       tt11394180
1        tt0108041
2        tt5164438
3       tt15204288
4        tt0139872
           ...    
5473     tt0113492
5474     tt0116669
5475     tt0147800
5476    tt14222534
5477     tt0892899
Name: id, Length: 5457, dtype: object

# new  id list = id_list

In [150]:
id_list = new_id_dataset_copy['id'].tolist()
print(len(id_list))



5457


In [14]:
other_ids = pd.read_csv('clean-movie.csv')
len(other_ids)

6666

In [15]:
other_id_list = other_ids['id'].tolist()
print(len(other_id_list))

6666


In [16]:
other_id_list_clean = []
for i in other_id_list:
    if i != "no_data":
        other_id_list_clean.append(i)


In [17]:
len(other_id_list_clean)

6405

In [18]:
only_new = []
for i in id_list:
    if i not in other_id_list_clean:
        only_new.append(i)

In [19]:
print(len(only_new ))

906


In [24]:
full_list = id_list.copy()
for i in other_id_list:
    if i not in id_list:
        full_list.append(i)
print(len(both))

4549


In [33]:
queried_df = pd.read_json('save_file - Copia copy.json')

In [39]:
queried_df.head(1)

id                     title originalTitle  \
0  tt0110668  Night of the Running Man                 

                         fullTitle   type    year  \
0  Night of the Running Man (1995)  Movie  1995.0   

                                               image releaseDate runtimeMins  \
0  https://m.media-amazon.com/images/M/MV5BMjgyZm...  1995-02-04          93   

  runtimeStr  ... images trailer  \
0   1h 33min  ...    NaN     NaN   

                                           boxOffice tagline  \
0  {'budget': '', 'openingWeekendUSA': '', 'gross...    None   

                                            keywords  \
0  murder of a nude woman,female nudity,nudity,bl...   

                                         keywordList  \
0  [murder of a nude woman, female nudity, nudity...   

                                            similars tvSeriesInfo  \
0  [{'id': 'tt0106850', 'title': 'Extreme Justice...         None   

  tvEpisodeInfo errorMessage  
0          None         None  

[1 rows x 47 columns]

In [46]:
queried_id = queried_df['id'].tolist()
x = set()
for i in queried_id:
    x.add(i)

In [47]:
print(queried_id[:7])
print(len(queried_id))
print(len(x))

['tt0110668', 'tt0119783', 'tt0044963', 'tt8060624', 'tt0031715', 'tt0272207', 'tt0341496']
2484
2484


In [52]:
y = set()
for i in id_list:
    y.add(i)
print(len(id_list))
print(len(y))

5457
5455


In [54]:
id_list_clean = []
for i in y:
    id_list_clean.append(i)
print(len(y))
print(len(id_list_clean))

5455
5455


In [55]:
id_to_query = []
for i in id_list_clean:
    if i not in queried_id:
        id_to_query.append(i)
print(len(id_to_query))

2971


In [57]:
print(len(id_list_clean))
print(len(queried_id))
print(5455-2484)

5455
2484
2971


In [58]:
import requests
json_list =[]
for id in id_to_query:


    #url = "https://imdb-api.com/en/API/Title/k_2xtxoo0v/"+id+"/Ratings,Awards"

    resp = requests.get(url)
    data = resp.json()
    json_list.append(data)
    if data == "None":
        break

    print(data['title'])


Bird Box
The Soul
Zaki Chan
Warrior Savitri
Suburra
F.R.E.D.I.
Phantom
The Iron Lady
The Game Changers
Being Mrs Elliot
The Mad Monk
What Keeps You Alive
Population 436
God Knows Where I Am
War on Everyone
Cirque du Freak: The Vampire's Assistant
Dolly Parton: A MusiCares Tribute
Love Jones
Ricos de Amor
The Brawler
Budapest
The Giant
Sticky Fingers
Terminator 3: Rise of the Machines
The Company Men
So Undercover
Doom
The Reason I Jump
The Man Who Would Be Polka King
Ocean's Twelve
Jis Desh Men Ganga Behti Hai
Oye Lucky! Lucky Oye!
The First Line
The Holy Man
Feel the Beat
Uppena
Mujhse Shaadi Karogi
Alexis Viera: A Story of Surviving
In the Tall Grass
Theo Who Lived
Insidious
Satte Pe Satta
Paying Guests
Unacknowledged
Mrs. Serial Killer
We the Animals
The Desert Bride
Small Town Crime
One Direction: This Is Us
Kung Fu Hustle
C Kkompany
Pope Francis: A Man of His Word
Prom Night
Twenty Bucks
The Death of Stalin
Raja Hindustani
Gunjan Saxena: The Kargil Girl
The Sea of Trees
Shark Nigh

In [163]:
queried_firstHalf_df = pd.read_json('first_half.json')
queried_firstHalf_df.head(1)

id                     title originalTitle  \
0  tt0110668  Night of the Running Man                 

                         fullTitle   type    year  \
0  Night of the Running Man (1995)  Movie  1995.0   

                                               image releaseDate runtimeMins  \
0  https://m.media-amazon.com/images/M/MV5BMjgyZm...  1995-02-04          93   

  runtimeStr  ... images trailer  \
0   1h 33min  ...    NaN     NaN   

                                           boxOffice tagline  \
0  {'budget': '', 'openingWeekendUSA': '', 'gross...    None   

                                            keywords  \
0  murder of a nude woman,female nudity,nudity,bl...   

                                         keywordList  \
0  [murder of a nude woman, female nudity, nudity...   

                                            similars tvSeriesInfo  \
0  [{'id': 'tt0106850', 'title': 'Extreme Justice...         None   

  tvEpisodeInfo errorMessage  
0          None         None  

[1 rows x 47 columns]

In [105]:
queried_secondHalf_df = pd.read_json('last_half.json')
queried_secondHalf_df.head(1)

id     title originalTitle        fullTitle   type    year  \
0  tt2737304  Bird Box                Bird Box (2018)  Movie  2018.0   

                                               image releaseDate  runtimeMins  \
0  https://m.media-amazon.com/images/M/MV5BMjAzMT...  2018-12-21        124.0   

  runtimeStr  ... images trailer  \
0    2h 4min  ...    NaN     NaN   

                                           boxOffice tagline  \
0  {'budget': '', 'openingWeekendUSA': '', 'gross...    None   

                                            keywords  \
0  suicide,survival,invisible creature,dystopia,s...   

                                         keywordList  \
0  [suicide, survival, invisible creature, dystop...   

                                            similars tvSeriesInfo  \
0  [{'id': 'tt6644200', 'title': 'A Quiet Place',...          NaN   

  tvEpisodeInfo errorMessage  
0          None         None  

[1 rows x 47 columns]

In [140]:
queried_secondHalf_df["id"] 

#print(queried_secondHalf_df.iloc[637])
print((queried_secondHalf_df["id"].iloc[2969]) == None)
print(queried_secondHalf_df["id"] == None)


True
0       False
1       False
2       False
3       False
4       False
        ...  
2966    False
2967    False
2968    False
2969    False
2970    False
Name: id, Length: 2971, dtype: bool


In [125]:
queried_secondHalf_df_copy = queried_secondHalf_df.copy()

In [141]:

#637 None, 1361 None these two ids were not foud
for index, item in queried_secondHalf_df_copy['id'].iteritems():
    if item == None:
        
        queried_secondHalf_df_copy.drop(index, inplace=True)
        print(index, item)

637 None
1361 None
2504 None
2505 None
2506 None
2507 None
2508 None
2509 None
2510 None
2511 None
2512 None
2513 None
2514 None
2515 None
2516 None
2517 None
2518 None
2519 None
2520 None
2521 None
2522 None
2523 None
2524 None
2525 None
2526 None
2527 None
2528 None
2529 None
2530 None
2531 None
2532 None
2533 None
2534 None
2535 None
2536 None
2537 None
2538 None
2539 None
2540 None
2541 None
2542 None
2543 None
2544 None
2545 None
2546 None
2547 None
2548 None
2549 None
2550 None
2551 None
2552 None
2553 None
2554 None
2555 None
2556 None
2557 None
2558 None
2559 None
2560 None
2561 None
2562 None
2563 None
2564 None
2565 None
2566 None
2567 None
2568 None
2569 None
2570 None
2571 None
2572 None
2573 None
2574 None
2575 None
2576 None
2577 None
2578 None
2579 None
2580 None
2581 None
2582 None
2583 None
2584 None
2585 None
2586 None
2587 None
2588 None
2589 None
2590 None
2591 None
2592 None
2593 None
2594 None
2595 None
2596 None
2597 None
2598 None
2599 None
2600 None
2601 None
2

In [142]:
queried_secondHalf_df_copy

id                                  title     originalTitle  \
0      tt2737304                               Bird Box                     
1     tt13598976                               The Soul            Ji hun   
2      tt0827788                              Zaki Chan         Zaky Chan   
3      tt4642936                        Warrior Savitri                     
4      tt4025514                                Suburra                     
...          ...                                    ...               ...   
2499   tt0280707                           Gosford Park                     
2500   tt2980648               The Hundred-Foot Journey                     
2501   tt0087960                        Prince Charming  Ching wa wong ji   
2502  tt10964430                                Thappad                     
2503  tt10857582  Los Tigres del Norte at Folsom Prison                     

                                         fullTitle   type    year  \
0                                  Bird Box (2018)  Movie  2018.0   
1                                  The Soul (2021)  Movie  2021.0   
2                                 Zaki Chan (2005)  Movie  2005.0   
3                           Warrior Savitri (2016)  Movie  2016.0   
4                                   Suburra (2015)  Movie  2015.0   
...                                            ...    ...     ...   
2499                           Gosford Park (2001)  Movie  2001.0   
2500               The Hundred-Foot Journey (2014)  Movie  2014.0   
2501                        Prince Charming (1984)  Movie  1984.0   
2502                                Thappad (2020)  Movie  2020.0   
2503  Los Tigres del Norte at Folsom Prison (2019)  Movie  2019.0   

                                                  image releaseDate  \
0     https://m.media-amazon.com/images/M/MV5BMjAzMT...  2018-12-21   
1     https://m.media-amazon.com/images/M/MV5BNGExNG...  2021-01-15   
2     https://m.media-amazon.com/images/M/MV5BOGIzMT...        None   
3     https://m.media-amazon.com/images/M/MV5BMzc0ND...  2016-08-25   
4     https://m.media-amazon.com/images/M/MV5BYzhmZT...  2015-10-14   
...                                                 ...         ...   
2499  https://m.media-amazon.com/images/M/MV5BYzM4Yz...  2002-01-18   
2500  https://m.media-amazon.com/images/M/MV5BMTQ3Mj...  2014-08-08   
2501  https://m.media-amazon.com/images/M/MV5BZWEyNW...  1984-04-18   
2502  https://m.media-amazon.com/images/M/MV5BNWQ1Yz...  2020-02-28   
2503  https://m.media-amazon.com/images/M/MV5BMDVjNj...  2019-09-15   

      runtimeMins runtimeStr  ... images trailer  \
0           124.0    2h 4min  ...    NaN     NaN   
1           130.0   2h 10min  ...    NaN     NaN   
2           114.0   1h 54min  ...    NaN     NaN   
3           136.0   2h 16min  ...    NaN     NaN   
4           130.0   2h 10min  ...    NaN     NaN   
...           ...        ...  ...    ...     ...   
2499        137.0   2h 17min  ...    NaN     NaN   
2500        122.0    2h 2min  ...    NaN     NaN   
2501         92.0   1h 32min  ...    NaN     NaN   
2502        142.0   2h 22min  ...    NaN     NaN   
2503         64.0    1h 4min  ...    NaN     NaN   

                                              boxOffice tagline  \
0     {'budget': '', 'openingWeekendUSA': '', 'gross...    None   
1     {'budget': '', 'openingWeekendUSA': '', 'gross...    None   
2     {'budget': '', 'openingWeekendUSA': '', 'gross...    None   
3     {'budget': '', 'openingWeekendUSA': '', 'gross...    None   
4     {'budget': '€7,000,000 (estimated)', 'openingW...    None   
...                                                 ...     ...   
2499  {'budget': '$19,800,000 (estimated)', 'opening...    None   
2500  {'budget': '$22,000,000 (estimated)', 'opening...    None   
2501  {'budget': '', 'openingWeekendUSA': '', 'gross...    None   
2502  {'budget': '', 'openingWeekendUSA': '', 'gross...    None   
2503  {'budget': '', 'openingWeekendUSA': '',

In [155]:
queried_first_id = queried_firstHalf_df['id'].tolist()
queried_second_id =queried_secondHalf_df_copy['id'].tolist()
print(len(queried_first_id))
print(len(queried_second_id))
print(2484 + 2502)

almost_complete = queried_first_id + queried_second_id
check_unique = set(almost_complete)

print(len(almost_complete))
print(len(check_unique))

print(len(id_list))
print(5457 - 4986)

2484
2502
4986
4986
4986
5457
471


In [156]:
to_query_last_bit = []
for i in id_list:
    if i not in almost_complete:
        to_query_last_bit.append(i)


In [157]:
print(len(to_query_last_bit))


469


In [159]:
import requests
json_list =[]
for id in to_query_last_bit:


    url = "https://imdb-api.com/en/API/Title/k_2xtxoo0v/"+id+"/Ratings,Awards"

    resp = requests.get(url)
    data = resp.json()
    json_list.append(data)
    

    print(data['title'])


Safe House
Schumacher
Blood Brothers: Malcolm X & Muhammad Ali
Rainbow
In the Cut
Shikara
An Unfinished Life
Cliffhanger
Cold Mountain
Green Lantern
House Party 2
Labyrinth
Mars Attacks!
The Blue Lagoon
Welcome Home, Roscoe Jenkins
Kyaa Kool Hai Hum
Untold: Caitlyn Jenner
Sweet Girl
The Piano
Vivo
'76
Beethoven's 2nd
Freedomland
Good Luck Chuck
Magnolia
Team America: World Police
The Last Boy Scout
The Machinist
The Original Kings of Comedy
The Last Mercenary
Fantastic Fungi
Deep
The Twilight Saga: New Moon
Twilight
A Perfect Fit
American Woman
Day of Destiny
Fear Street: Part Two - 1978
Finding Hubby
Last Summer
Mama Drama
Mortal Kombat
Not Another Teen Movie
Seven Pounds
The American
The Long Riders
Love Is a Story
Fatherhood
Aziza
Security
Life of Crime
Sir! No Sir!
Picture a Scientist
Dancing Queens
American Outlaws
Domestic Disturbance
Flipped
Gold Statue
Mosquita y Mari
Never Back Down 2: The Beatdown
Starsky & Hutch
Blue Miracle
State of Play
The Sweetest Thing
The Whole Nine Ya

In [160]:
json_list

[{'id': 'tt1599348',
  'title': 'Safe House',
  'originalTitle': '',
  'fullTitle': 'Safe House (2012)',
  'type': 'Movie',
  'year': '2012',
  'image': 'https://m.media-amazon.com/images/M/MV5BMjI5ODkyMjA2Nl5BMl5BanBnXkFtZTcwNTcyNTgzNw@@._V1_Ratio0.6762_AL_.jpg',
  'releaseDate': '2012-02-10',
  'runtimeMins': '115',
  'runtimeStr': '1h 55min',
  'plot': 'A young CIA agent is tasked with looking after a fugitive in a safe house. But when the safe house is attacked, he finds himself on the run with his charge.',
  'plotLocal': '',
  'plotLocalIsRtl': False,
  'awards': 'Awards, 1 win & 7 nominations',
  'directors': 'Daniel Espinosa',
  'directorList': [{'id': 'nm1174251', 'name': 'Daniel Espinosa'}],
  'writers': 'David Guggenheim',
  'writerList': [{'id': 'nm1638756', 'name': 'David Guggenheim'}],
  'stars': 'Denzel Washington, Ryan Reynolds, Robert Patrick',
  'starList': [{'id': 'nm0000243', 'name': 'Denzel Washington'},
   {'id': 'nm0005351', 'name': 'Ryan Reynolds'},
   {'id': 'n

In [162]:
import json

filename = 'last_bit.json'          #use the file extension .json
with open(filename, 'w') as file_object:  #open the file in write mode
 json.dump(json_list, file_object)